<a href="https://colab.research.google.com/github/zoviedo/Lab2-EstructuraDeDatos/blob/main/Lab2_EstructuraDeDatos2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#LABORATORIO 2: GRAFOS
Integrantes: Franklin Amador, Zharick Oviedo, Vanessa Diaz y Gabriel Palencia

#Librerias

In [ ]:
# Librerias necesarias

from IPython.display import IFrame
import folium
from geographiclib.geodesic import Geodesic
from geopy.distance import geodesic
from heapq import heappop, heappush
import pandas as pd
import heapq
import networkx as nx

#Creacion del DataFrame

In [ ]:
"""
Se toma un Dataframe con vuelos repetidos y con vuelos de ida y vuelta identicos
como se hará un grafo simple, se necesita un unico vuelo y se entiende
como que funciona en ambas direcciones
"""

def eliminar_vuelos_iguales(df):
  # Eliminar las filas idénticas del DataFrame original
  df = df.drop_duplicates()

  # Crear una nueva columna que contenga la conexión única
  df['Connection'] = df.apply(lambda row: frozenset([row['Source Airport Code'], row['Destination Airport Code']]), axis=1)

  # Eliminar registros duplicados usando la columna 'Connection'
  df_unique = df.drop_duplicates(subset='Connection')

  # Eliminar la columna 'Connection' en el DataFrame resultante
  df_unique = df_unique.drop(columns='Connection')

  return df_unique


In [ ]:
# Ruta donde se encuentra el archivo con la informacion
ruta = "flights_final.csv"

# Creacion del DataFrame a partir del archivo
df = pd.read_csv(ruta)

# Se eliminan los vuelos iguales en ambas direcciones (A-B) = (B-A)
df = eliminar_vuelos_iguales(df)


<ipython-input-2-371f03e0ba6c>:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Connection'] = df.apply(lambda row: frozenset([row['Source Airport Code'], row['Destination Airport Code']]), axis=1)


In [ ]:
# A partir del df original se reduce para obtener
# uno en el que no se repitan aeropuertos

def obtener_df_completo(df_original):

    # Crear DataFrames con la información de origen y destino
    df_origen = df_original[[
        'Source Airport Code', 'Source Airport Name', 'Source Airport City',
        'Source Airport Country', 'Source Airport Latitude', 'Source Airport Longitude'
    ]]

    df_destino = df_original[[
        'Destination Airport Code', 'Destination Airport Name', 'Destination Airport City',
        'Destination Airport Country', 'Destination Airport Latitude', 'Destination Airport Longitude'
    ]]

    # Cambiar los nombres de las columnas para que coincidan
    df_origen.columns = ['Airport Code', 'Airport Name', 'Airport City', 'Airport Country', 'Latitude', 'Longitude']
    df_destino.columns = ['Airport Code', 'Airport Name', 'Airport City', 'Airport Country', 'Latitude', 'Longitude']

    # Eliminar los aeropuertos duplicados en ambos DataFrames
    df_origen = df_origen.drop_duplicates()
    df_destino = df_destino.drop_duplicates()

    # Unir los DataFrames df_origen y df_destino
    df_completo = pd.concat([df_origen, df_destino], ignore_index=True)

    # Eliminar aeropuertos duplicados en el DataFrame combinado
    df_completo = df_completo.drop_duplicates()

    return df_completo


#Lista de objetos aeropuerto

In [ ]:
# Creacion clase Aeropuerto
class Aeropuerto:
  def __init__(self, code, name, city, country, latitude, longitude):
    self.code = code
    self.name = name
    self.city = city
    self.country = country
    self.latitude = latitude
    self.longitude = longitude


# Creacion de una lista con todos los aeropuertos
# se utiliza un df donde no hay aeropuertos repetidos
def crear_lista_aeropuertos(df_completo):
    aeropuertos = set()  # Usar un conjunto para eliminar duplicados
    for index, row in df_completo.iterrows():
        aeropuerto = Aeropuerto(
            row['Airport Code'],
            row['Airport Name'],
            row['Airport City'],
            row['Airport Country'],
            row['Latitude'],
            row['Longitude']
        )
        aeropuertos.add(aeropuerto)
    return list(aeropuertos)


# Buscar aeropuerto a partir del codigo
def buscar_aeropuerto_por_codigo(codigo, aeropuertos):
  for aeropuerto in aeropuertos:
    if aeropuerto.code == codigo:
      return True
    return False


# Escribir la informacion de un objeto tipo aeropuerto
def imprimir_datos_aeropuerto(aeropuerto):
    print(f"Código: {aeropuerto.code}")
    print(f"Nombre: {aeropuerto.name}")
    print(f"Ciudad: {aeropuerto.city}")
    print(f"País: {aeropuerto.country}")
    print(f"Latitud: {aeropuerto.latitude}")
    print(f"Longitud: {aeropuerto.longitude}")

#Calcular distancia entre 2 puntos geograficos

In [ ]:
# Calcular distancia utilizando el metodo de Karney
def calculate_distance_karney(lat1, lon1, lat2, lon2):
    # Crea una instancia de Geodesic con el método de Karney
    geod = Geodesic.WGS84.Inverse(lat1, lon1, lat2, lon2)

    # La distancia estará en el atributo 's12' en metros
    distance_karney = geod['s12']

    return distance_karney

#Clase Grafo


In [ ]:
# Creacion clase grafo
class Grafo:
    def __init__(self, aeropuertos: list):
        self.nodos_cod = {aeropuerto.code: aeropuerto for aeropuerto in aeropuertos}
        self.nodos_indices = {codigo: i for i, codigo in enumerate(self.nodos_cod.keys())}
        self.num_nodos = len(aeropuertos)
        self.matriz_adyacencia = [[0] * self.num_nodos for _ in range(self.num_nodos)]


    # Se llena la matriz de adyacencia con todas las distancias entre los aeropuertos
    def llenar_grafo(self, df_original):
        codigos_origen = df_original['Source Airport Code'].values
        codigos_destino = df_original['Destination Airport Code'].values
        distances = {}

        # Calcular distancias únicas
        for _, row in df_original.iterrows():
            codigo_origen = row['Source Airport Code']
            codigo_destino = row['Destination Airport Code']
            lat1 = row['Source Airport Latitude']
            lon1 = row['Source Airport Longitude']
            lat2 = row['Destination Airport Latitude']
            lon2 = row['Destination Airport Longitude']

            # Calcular la distancia geográfica
            distancia = calculate_distance_karney(lat1, lon1, lat2, lon2)

            # Almacenar la distancia en el diccionario de distancias
            distances[(codigo_origen, codigo_destino)] = distancia

        for i in range(len(codigos_origen)):
            codigo_origen = codigos_origen[i]
            codigo_destino = codigos_destino[i]

            # Obtener los índices de los nodos a partir de sus códigos
            indice_origen = self.nodos_indices[codigo_origen]
            indice_destino = self.nodos_indices[codigo_destino]

            # Obtener la distancia desde el diccionario de distancias
            distancia = distances[(codigo_origen, codigo_destino)]

            # Establecer la conexión (arista) con el peso (distancia) entre los nodos
            self.matriz_adyacencia[indice_origen][indice_destino] = distancia
            self.matriz_adyacencia[indice_destino][indice_origen] = distancia


    # Retorna la distancia entre 2 aeropuertos a partir de sus codigos
    def obtener_conexion(self, cod_origen, cod_destino):
        if cod_origen not in self.nodos_cod or cod_destino not in self.nodos_cod:
            return 0  # Códigos de aeropuerto no válidos (NONE - 0)
        indice_origen = self.nodos_indices[cod_origen]
        indice_destino = self.nodos_indices[cod_destino]
        return self.matriz_adyacencia[indice_origen][indice_destino]


    # Implementación de Dijkstra
    def dijkstra(self, inicio, fin):
        if inicio not in self.nodos_cod or fin not in self.nodos_cod:
            return None  # Códigos de aeropuerto no válidos

        distancias = {codigo: float('inf') for codigo in self.nodos_cod}
        distancias[inicio] = 0
        visitados = set()

        while visitados != set(self.nodos_cod):
            nodo_actual = None
            for codigo in self.nodos_cod:
                if codigo not in visitados and (nodo_actual is None or distancias[codigo] < distancias[nodo_actual]):
                    nodo_actual = codigo

            if distancias[nodo_actual] == float('inf'):
                break  # No se pudo encontrar un camino

            visitados.add(nodo_actual)

            for vecino in self.nodos_cod:
                if self.matriz_adyacencia[self.nodos_indices[nodo_actual]][self.nodos_indices[vecino]] > 0:
                    distancia = distancias[nodo_actual] + self.matriz_adyacencia[self.nodos_indices[nodo_actual]][self.nodos_indices[vecino]]
                    if distancia < distancias[vecino]:
                        distancias[vecino] = distancia

        if distancias[fin] == float('inf'):
            return None  # No se pudo encontrar un camino válido

        ruta_mas_corta = [fin]
        while fin != inicio:
            for codigo in self.nodos_cod:
                if self.matriz_adyacencia[self.nodos_indices[fin]][self.nodos_indices[codigo]] > 0:
                    if distancias[fin] == distancias[codigo] + self.matriz_adyacencia[self.nodos_indices[fin]][self.nodos_indices[codigo]]:
                        ruta_mas_corta.insert(0, codigo)
                        fin = codigo
                        break

        return ruta_mas_corta  # Retorna los códigos de los aeropuertos en la ruta


    # Muestra el camino minimo entre 2 aeropuertos
    def mostrar_camino_minimo(self, cod_origen, cod_destino):
        camino_minimo = self.dijkstra(cod_origen, cod_destino)
        if not camino_minimo:
            return "No se puede encontrar un camino válido entre los aeropuertos especificados."

        distancia_total = 0
        descripcion_camino = ""
        for i, codigo in enumerate(camino_minimo):
            nodo = self.nodos_cod[codigo]
            descripcion_camino += codigo
            if i < len(camino_minimo) - 1:
                descripcion_camino += " - "
                siguiente_codigo = camino_minimo[i + 1]
                distancia_total += self.obtener_conexion(codigo, siguiente_codigo)
            print(f"Posición {i}:")
            print(f"Código: {nodo.code}")
            print(f"Nombre: {nodo.name}")
            print(f"Ciudad: {nodo.city}")
            print(f"País: {nodo.country}")
            print(f"Latitud: {nodo.latitude}")
            print(f"Longitud: {nodo.longitude}")
            print("")

        print(f"Recorrido: {descripcion_camino}")
        print(f"Distancia total: {distancia_total} metros")
        print("Camino mínimo mostrado con éxito.")


    # Crea el mapa visual a partir del camino minimo
    def crear_mapa_aeropuertos(self, camino_minimo):
        mapa = folium.Map(location=[lista_aeropuertos[0].latitude, lista_aeropuertos[0].longitude], zoom_start=4)
        coordenadas_camino = []

        # Agregar marcadores para cada aeropuerto en el camino
        for codigo in camino_minimo:
            aeropuerto = self.nodos_cod[codigo]
            coordenadas_camino.append([aeropuerto.latitude, aeropuerto.longitude])
            folium.Marker(
                location=[aeropuerto.latitude, aeropuerto.longitude],
                popup=f"{aeropuerto.code} - {aeropuerto.name}",
                icon=folium.Icon(icon="plane", prefix="fa", icon_color='green', icon_size=(10, 10))
            ).add_to(mapa)

        # Agregar líneas para conectar los aeropuertos en el camino
        folium.PolyLine(
            locations=coordenadas_camino,
            color='black',
            weight=2,
        ).add_to(mapa)

        return mapa


    # Muestra el camino minimo visualmente en el mapa
    def mostrar_camino_minimo_en_mapa(self, cod_origen, cod_destino):
        camino_minimo = self.dijkstra(cod_origen, cod_destino)
        if not camino_minimo:
            return None

        mapa_aeropuertos = self.crear_mapa_aeropuertos(camino_minimo)
        for i in range(len(camino_minimo) - 1):
            aeropuerto_actual = self.nodos_cod[camino_minimo[i]]
            siguiente_aeropuerto = self.nodos_cod[camino_minimo[i + 1]]
            folium.PolyLine(
                locations=[(aeropuerto_actual.latitude, aeropuerto_actual.longitude),
                           (siguiente_aeropuerto.latitude, siguiente_aeropuerto.longitude)],
                color='black',
                weight=2,
            ).add_to(mapa_aeropuertos)

        return mapa_aeropuertos


# Clase Grafo utilizando Network


In [ ]:
# Creacion del grafo
G = nx.Graph()

# Se obtiene un df sin ningún aeropuerto repetido
df_new = obtener_df_completo(df)

# Crear la lista de aeropuertos
lista_aeropuertos = crear_lista_aeropuertos(df_new)

# Instanciamiento del grafo
grafo = Grafo(lista_aeropuertos)
grafo.llenar_grafo(df)

# Lista con los codigos de cada aeropuerto
codigos_aeropuerto = [aeropuerto.code for aeropuerto in lista_aeropuertos]

# Agrega los códigos de aeropuerto como nodos al grafo
G.add_nodes_from(codigos_aeropuerto)

# Itera a través de las filas del DataFrame
for index, row in df.iterrows():
    origen = row['Source Airport Code']
    destino = row['Destination Airport Code']
    latitud_origen = row['Source Airport Latitude']
    longitud_origen = row['Source Airport Longitude']
    latitud_destino = row['Destination Airport Latitude']
    longitud_destino = row['Destination Airport Longitude']

    # Calcula la distancia utilizando tu función de cálculo de distancia
    distancia = calculate_distance_karney(latitud_origen, longitud_origen, latitud_destino, longitud_destino)

    # Agrega el borde al grafo con el atributo de peso (weight) igual a la distancia calculada
    G.add_edge(origen, destino, weight=distancia)


In [ ]:
# Encuentra los caminos minimos mas largos de un aeropuerto
def find_longest_paths(G, source, n=10):
    longest_paths = []

    def dfs_longest_paths(path):
        nonlocal longest_paths
        if len(path) > 1:
            length = sum(G[path[i]][path[i + 1]]['weight'] for i in range(len(path) - 1))
            longest_paths.append((path, length))
        if len(longest_paths) >= n:
            return
        for neighbor in G.neighbors(path[-1]):
            if neighbor not in path:
                dfs_longest_paths(path + [neighbor])

    for neighbor in G.neighbors(source):
        dfs_longest_paths([source, neighbor])

    longest_paths = sorted(longest_paths, key=lambda x: x[1], reverse=True)[:n]
    return longest_paths


# Escribe informacion de un aeropuerto dado su codigo desde un df
def imprimir_aeropuerto_df(codigo, df):
  aeropuerto_info = df[df['Source Airport Code'] == codigo]
  if not aeropuerto_info.empty:
    aeropuerto = aeropuerto_info.iloc[0]  # Tomar la primera fila (asumiendo que no hay duplicados)
    print(f"Código: {aeropuerto['Source Airport Code']}")
    print(f"Nombre: {aeropuerto['Source Airport Name']}")
    print(f"Ciudad: {aeropuerto['Source Airport City']}")
    print(f"País: {aeropuerto['Source Airport Country']}")
    print(f"Latitud: {aeropuerto['Source Airport Latitude']}")
    print(f"Longitud: {aeropuerto['Source Airport Longitude']}")
  else:
    print(f"No se encontró un aeropuerto con el código {codigo}")


# Escribe los 10 caminos minimos mas largos y su info
def imprimir_caminos(cod_origen, longest_paths, df):
  print("\nAeropuerto de origen")
  imprimir_aeropuerto_df(cod_origen, df)

  # Imprime los 10 caminos más largos
  for i, (path, length) in enumerate(longest_paths):
      aeropuerto_final = path[-1]
      print(f"\nAeropuerto {i+1}")

      imprimir_aeropuerto_df(path[-1], df)

      print(f"Camino {i + 1}: {path}")
      print(f"Longitud del camino: {length} unidades")
      print("")


#Mapa con todos los aeropuertos

In [ ]:
# Definir una función para crear un mapa con marcadores para cada aeropuerto en la lista
def crear_mapa_aeropuertos(lista_aeropuertos, matriz_adyacencia):
    mapa = folium.Map(location=[lista_aeropuertos[0].latitude, lista_aeropuertos[0].longitude], zoom_start=4)

    # Agregar marcadores para cada aeropuerto en la lista
    for aeropuerto in lista_aeropuertos:
        folium.Marker(
            location=[aeropuerto.latitude, aeropuerto.longitude],
            popup=f"{aeropuerto.code} {aeropuerto.name}",
            icon=folium.Icon(icon="plane", prefix="fa", icon_color='green', icon_size=(10, 10))
        ).add_to(mapa)

    return mapa

df_completo = obtener_df_completo(df)
lista_aeropuertos = crear_lista_aeropuertos(df_completo)
mapa_aeropuertos = crear_mapa_aeropuertos(lista_aeropuertos, grafo.matriz_adyacencia)
display(mapa_aeropuertos)

# Ejemplo: los 10 caminos minimos mas largos de un aeropuerto



Mostrar la información (código, nombre, ciudad, país, latitud y longitud)
de los 10 aeropuertos cuyos caminos mínimos desde el vértice dado sean
los más largos.

Se debe mostrar la distancia de los
caminos

In [ ]:
# Codigo de origen
cod_origen = "COK"

# Obtiene los caminos mas largos
longest_paths = find_longest_paths(G, cod_origen, n=10)

# Se escriben los 10 caminos minimos mas largos
imprimir_caminos(cod_origen, longest_paths, df)

#Ejemplo: camino minimo entre 2 aeropuertos:



Mostrar el camino mínimo entre el primer y el segundo vértice sobre el
mapa de la interfaz gráfica, pasando por cada uno de los vértices
intermedios del camino.

Mostrar info de todos los vertices (código, nombre, ciudad, país, latitud y
longitud).

In [ ]:
#Camino minimo entre 2 aeropuertos

cod_origen = "COK"  # Código de aeropuerto de origen
cod_destino = "ATL"  # Código de aeropuerto de destino

# Probar el método mostrar_camino_minimo
grafo.mostrar_camino_minimo(cod_origen, cod_destino)
mapita = grafo.mostrar_camino_minimo_en_mapa(cod_origen, cod_destino)
display(mapita)

#Menú de opciones

In [ ]:
# Funcion general donde se ejecuta todo el codigo

def menu_principal(grafo):
    opt = 0
    aeropuerto_encontrado = False
    while opt != 3:
        print("\nBienvenido al sistema de información de vuelos")
        print("Seleccione una opción:")
        print("1. Consultar información de un aeropuerto y mostrar los 10 caminos mínimos más largos desde este.")
        print("2. Mostrar el camino mínimo entre dos aeropuertos sobre el mapa.")
        print("3. Salir")

        try:
            opt = int(input("\n"))
        except ValueError:
            print("Opción no válida, intente de nuevo.")
            opt = 0  # Se mantiene en el menú principal
        if opt == 1:
          print("\nIngrese el código del aeropuerto que desea consultar:")
          codigo_aeropuerto = input("\n")
          if codigo_aeropuerto in grafo.nodos_cod:
              aeropuerto_origen = grafo.nodos_cod[codigo_aeropuerto]
              print("\nInformación del aeropuerto con código:", codigo_aeropuerto, "\n")
              imprimir_datos_aeropuerto(aeropuerto_origen)

              longest_paths = find_longest_paths(G, codigo_aeropuerto, n=10)
              imprimir_caminos(codigo_aeropuerto, longest_paths, df)
          else:
            print("Aeropuerto con código", codigo_aeropuerto, "no encontrado en la lista de aeropuertos.")
            pass
        elif opt == 2:
            if aeropuerto_origen:  # aeropuerto_origen se define en la opción 1
                print(f"Desea consultar información de un aeropuerto destino con respecto al aeropuerto: {codigo_aeropuerto}? (Si = 1/No = 2)")
                respuesta = 0
                while respuesta != 1 and respuesta != 2:
                    try:
                        respuesta = int(input())
                    except ValueError:
                        print("Opción no válida, intente de nuevo.")
                        respuesta = 0
                    if respuesta == 1:
                        print("Ingrese el código del aeropuerto de destino:")
                        codigo_aeropuerto_destino = input()
                        if codigo_aeropuerto_destino in grafo.nodos_cod and codigo_aeropuerto_destino != codigo_aeropuerto:
                            grafo.mostrar_camino_minimo(codigo_aeropuerto, codigo_aeropuerto_destino)
                            mapita = grafo.mostrar_camino_minimo_en_mapa(codigo_aeropuerto, codigo_aeropuerto_destino)
                            display(mapita)

                            if codigo_aeropuerto_destino == codigo_aeropuerto:
                              print("El aeropuerto de destino no puede ser el mismo que el aeropuerto de origen.")
                            else:
                                print("Aeropuerto de destino no encontrado en la lista de aeropuertos.")
                    else:
                        opt = 0  # Volver al menú principal
            else:
                print("Aún no se ha consultado ningún aeropuerto de origen en la opción 1. Por favor, ejecute la opción 1 primero.")
            pass
        elif opt == 3:
            print("Gracias por usar el sistema de información de vuelos.")
        else:
            print("Opción no válida, intente una opción entre (1 - 3).")
            opt = 0  # Se mantiene en el menú principal

# Llamar a la función menu_principal con el grafo como argumento
menu_principal(grafo)


Bienvenido al sistema de información de vuelos
Seleccione una opción:
1. Consultar información de un aeropuerto y mostrar los 10 caminos mínimos más largos desde este.
2. Mostrar el camino mínimo entre dos aeropuertos sobre el mapa.
3. Salir

3
Gracias por usar el sistema de información de vuelos.
